In [1]:
# Import dependencies

# data analysis and wrangling

import pandas as pd
import numpy as np
import math
import os
from datetime import datetime, timedelta
from statistics import mean

# visualization

import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

# machine learning

In [2]:
# Set pandas options

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)
pd.options.mode.chained_assignment = None  # default='warn'

In [3]:
# Read data files

data_files = ['train.csv', 'test.csv', 'weather_train.csv', 'weather_test.csv', 'building_metadata.csv']
raw_df = {}

for file in data_files:
    raw_df[file[:-4]] = pd.read_csv(os.path.join(os.getcwd(), 'data', file))

# Classifying
We may want to classify or categorize our samples. We may also want to understand the implications or correlation of different classes with our solution goal.

In [4]:
# Function to examine and return missing data from a dataframe as a percentage

def missingdata(data):
    total = data.isnull().sum().sort_values(ascending = False)
    percent = (data.isnull().sum()/data.isnull().count()*100).sort_values(ascending = False)
    ms=pd.concat([total, percent], axis=1, keys=['Total', 'Percent'])
    ms= ms[ms["Percent"] > 0]

    return ms

In [5]:
# Preview the data

# Train & Test data

train_df = raw_df['train'].copy()
test_df = raw_df['test'].copy()

train_df.info(verbose=True, show_counts=True)
print('-'*40)
test_df.info(verbose=True, show_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20216100 entries, 0 to 20216099
Data columns (total 4 columns):
 #   Column         Non-Null Count     Dtype  
---  ------         --------------     -----  
 0   building_id    20216100 non-null  int64  
 1   meter          20216100 non-null  int64  
 2   timestamp      20216100 non-null  object 
 3   meter_reading  20216100 non-null  float64
dtypes: float64(1), int64(2), object(1)
memory usage: 616.9+ MB
----------------------------------------
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 41697600 entries, 0 to 41697599
Data columns (total 4 columns):
 #   Column       Non-Null Count     Dtype 
---  ------       --------------     ----- 
 0   row_id       41697600 non-null  int64 
 1   building_id  41697600 non-null  int64 
 2   meter        41697600 non-null  int64 
 3   timestamp    41697600 non-null  object
dtypes: int64(3), object(1)
memory usage: 1.2+ GB


In [6]:
train_df

building_id  meter            timestamp  meter_reading
0                   0      0  2016-01-01 00:00:00          0.000
1                   1      0  2016-01-01 00:00:00          0.000
2                   2      0  2016-01-01 00:00:00          0.000
3                   3      0  2016-01-01 00:00:00          0.000
4                   4      0  2016-01-01 00:00:00          0.000
...               ...    ...                  ...            ...
20216095         1444      0  2016-12-31 23:00:00          8.750
20216096         1445      0  2016-12-31 23:00:00          4.825
20216097         1446      0  2016-12-31 23:00:00          0.000
20216098         1447      0  2016-12-31 23:00:00        159.575
20216099         1448      0  2016-12-31 23:00:00          2.850

[20216100 rows x 4 columns]

In [7]:
missingdata(train_df)

Empty DataFrame
Columns: [Total, Percent]
Index: []

In [8]:
missingdata(test_df)

Empty DataFrame
Columns: [Total, Percent]
Index: []

In [9]:
# Weather train & Weather test data

weather_train_df = raw_df['weather_train'].copy()
weather_test_df = raw_df['weather_test'].copy()

weather_train_df.info(verbose=True, show_counts=True)
print('-'*40)
weather_test_df.info(verbose=True, show_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 139773 entries, 0 to 139772
Data columns (total 9 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   site_id             139773 non-null  int64  
 1   timestamp           139773 non-null  object 
 2   air_temperature     139718 non-null  float64
 3   cloud_coverage      70600 non-null   float64
 4   dew_temperature     139660 non-null  float64
 5   precip_depth_1_hr   89484 non-null   float64
 6   sea_level_pressure  129155 non-null  float64
 7   wind_direction      133505 non-null  float64
 8   wind_speed          139469 non-null  float64
dtypes: float64(7), int64(1), object(1)
memory usage: 9.6+ MB
----------------------------------------
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 277243 entries, 0 to 277242
Data columns (total 9 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   site_id             27

In [10]:
weather_train_df

site_id            timestamp  air_temperature  cloud_coverage  dew_temperature  precip_depth_1_hr  sea_level_pressure  wind_direction  wind_speed
0             0  2016-01-01 00:00:00             25.0             6.0             20.0                NaN              1019.7             0.0         0.0
1             0  2016-01-01 01:00:00             24.4             NaN             21.1               -1.0              1020.2            70.0         1.5
2             0  2016-01-01 02:00:00             22.8             2.0             21.1                0.0              1020.2             0.0         0.0
3             0  2016-01-01 03:00:00             21.1             2.0             20.6                0.0              1020.1             0.0         0.0
4             0  2016-01-01 04:00:00             20.0             2.0             20.0               -1.0              1020.0           250.0         2.6
...         ...                  ...              ...             ...              ...                ...                 ...             ...         ...
139768       15  2016-12-31 19:00:00              3.0             NaN             -8.0                NaN                 NaN           180.0         5.7
139769       15  2016-12-31 20:00:00              2.8             2.0             -8.9                NaN              1007.4           180.0         7.7
139770       15  2016-12-31 21:00:00              2.8             NaN             -7.2                NaN              1007.5           180.0         5.1
139771       15  2016-12-31 22:00:00              2.2             NaN             -6.7                NaN              1008.0           170.0         4.6
139772       15  2016-12-31 23:00:00              1.7             NaN             -5.6               -1.0              1008.5           180.0         8.8

[139773 rows x 9 columns]

In [11]:
missingdata(weather_train_df)

Total    Percent
cloud_coverage      69173  49.489529
precip_depth_1_hr   50289  35.979052
sea_level_pressure  10618   7.596603
wind_direction       6268   4.484414
wind_speed            304   0.217496
dew_temperature       113   0.080845
air_temperature        55   0.039350

In [12]:
missingdata(weather_test_df)

Total    Percent
cloud_coverage      140448  50.658808
precip_depth_1_hr    95588  34.478057
sea_level_pressure   21265   7.670167
wind_direction       12370   4.461790
wind_speed             460   0.165919
dew_temperature        327   0.117947
air_temperature        104   0.037512

In [13]:
# Building metadata

building_df = raw_df['building_metadata'].copy()

building_df.info(verbose=True, show_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1449 entries, 0 to 1448
Data columns (total 6 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   site_id      1449 non-null   int64  
 1   building_id  1449 non-null   int64  
 2   primary_use  1449 non-null   object 
 3   square_feet  1449 non-null   int64  
 4   year_built   675 non-null    float64
 5   floor_count  355 non-null    float64
dtypes: float64(2), int64(3), object(1)
memory usage: 68.0+ KB


In [14]:
building_df

site_id  building_id                    primary_use  square_feet  year_built  floor_count
0           0            0                      Education         7432      2008.0          NaN
1           0            1                      Education         2720      2004.0          NaN
2           0            2                      Education         5376      1991.0          NaN
3           0            3                      Education        23685      2002.0          NaN
4           0            4                      Education       116607      1975.0          NaN
...       ...          ...                            ...          ...         ...          ...
1444       15         1444  Entertainment/public assembly        19619      1914.0          NaN
1445       15         1445                      Education         4298         NaN          NaN
1446       15         1446  Entertainment/public assembly        11265      1997.0          NaN
1447       15         1447            Lodging/residential        29775      2001.0          NaN
1448       15         1448                         Office        92271      2001.0          NaN

[1449 rows x 6 columns]

In [15]:
missingdata(building_df)

Total    Percent
floor_count   1094  75.500345
year_built     774  53.416149

# Charting
How to select the right visualization plots and charts depending on nature of the data and the solution goals.

# Correcting
We may also analyze the given training dataset for errors or possibly inaccurate values within features and try to correct these values or exclude the samples containing the errors. One way to do this is to detect any outliers among our samples or features. We may also completely discard a feature if it is not contributing to the analysis or may significantly skew the results.

In [16]:
# Correcting by dropping features with a lot of missing data

weather_drop = ['cloud_coverage', 'precip_depth_1_hr', 'sea_level_pressure']
building_drop = ['floor_count', 'year_built']

weather_train_df.drop(weather_drop, axis=1, inplace=True)
weather_test_df.drop(weather_drop, axis=1, inplace=True)
building_df.drop(building_drop, axis=1, inplace=True)

# Completing
Data preparation may also require us to estimate any missing values within a feature. Model algorithms may work best when there are no missing values.

In [17]:
# Function to estimate weather null values based on the averages of 
# the previous and post known values

def estimate_weather(df, col):
    null_dex = list(df.loc[df[col].isna()]['timestamp'].index)
    for dex in null_dex:
        if math.isnan(df[col][dex+1]):
            df[col][dex] = df[col][dex-1].copy()
        else:
            df[col][dex] = round(mean([df[col][dex-1],df[col][dex+1]]), 1).copy()
    return df[col]

In [18]:
# Estimating the values for weather data using the average from the previous & following hour

weather_combined = [weather_train_df, weather_test_df]
col_to_complete = ['wind_direction', 'wind_speed', 'dew_temperature', 'air_temperature']

for w_df in weather_combined:
    for c in col_to_complete:
        w_df[c] = estimate_weather(w_df, c)

# Creating
Can we create new features based on an existing feature or a set of features, such that the new feature follows the correlation, conversion, completeness goals.

In [38]:
# Creating new humidity feature calculated from air & dew temperature

# Calculation formula source: https://www.weather.gov/media/epz/wxcalc/vaporPressure.pdf

weather_combined = [weather_train_df, weather_test_df]

for w_df in weather_combined:
    rh_list = []
    for i in range(0,len(w_df)):
        e_s = 6.11 * 10 * ((7.5 * w_df['air_temperature'][i])/(237.3 + w_df['air_temperature'][i]))
        e = 6.11 * 10 * ((7.5 * w_df['dew_temperature'][i])/(237.3 + w_df['dew_temperature'][i]))

        rh_list.append(round(e / e_s * 100, 1))
    w_df['relative_humidity'] = rh_list

<ipython-input-38-cb8b7db1d083>:13: RuntimeWarning: divide by zero encountered in double_scalars
  rh_list.append(round(e / e_s * 100, 1))
<ipython-input-38-cb8b7db1d083>:13: RuntimeWarning: invalid value encountered in double_scalars
  rh_list.append(round(e / e_s * 100, 1))


In [45]:
for i in range(0,len(weather_train_df)):
    print(str(i) + ', ', str(w_df['air_temperature'][i]) + ', ' + str(w_df['dew_temperature'][i]) + ',' + str(6.11 * 10 * ((7.5 * w_df['air_temperature'][i])/(237.3 + w_df['air_temperature'][i]))))

0, ,  17.8, 11.7,31.975107800862403
1, ,  17.8, 12.8,31.975107800862403
2, ,  16.1, 12.8,29.11533149171271
3, ,  17.2, 13.3,30.97013752455796
4, ,  16.7, 13.3,30.129035433070868
5, ,  15.6, 12.8,28.26690391459075
6, ,  15.0, 12.8,27.24435196195006
7, ,  15.0, 13.3,27.24435196195006
8, ,  13.3, 12.2,24.320530726256983
9, ,  12.2, 11.7,22.407414829659317
10, ,  13.9, 12.8,25.356986464968152
11, ,  13.9, 12.8,25.356986464968152
12, ,  12.2, 11.1,22.407414829659317
13, ,  13.3, 12.2,24.320530726256983
14, ,  17.8, 15.0,31.975107800862403
15, ,  22.8, 15.6,40.16955017301038
16, ,  23.9, 16.1,41.930225880551305
17, ,  25.6, 16.7,44.62228984404716
18, ,  25.6, 16.1,44.62228984404716
19, ,  26.7, 15.6,46.34573863636364
20, ,  27.2, 16.1,47.12438563327032
21, ,  26.7, 16.1,46.34573863636364
22, ,  26.1, 16.1,45.40746013667425
23, ,  23.3, 15.6,40.97169992325403
24, ,  21.7, 17.2,38.39391891891892
25, ,  21.1, 17.2,37.419020897832816
26, ,  20.6, 17.2,36.60314075222954
27, ,  20.6, 17.2,36.60314

894, ,  16.1, 14.4,29.11533149171271
895, ,  15.0, 13.3,27.24435196195006
896, ,  14.4, 13.3,26.216924910607865
897, ,  15.6, 14.4,28.26690391459075
898, ,  15.6, 13.9,28.26690391459075
899, ,  15.6, 14.4,28.26690391459075
900, ,  15.6, 14.4,28.26690391459075
901, ,  15.0, 14.4,27.24435196195006
902, ,  19.4, 16.1,34.6320607713284
903, ,  22.8, 15.6,40.16955017301038
904, ,  24.4, 15.6,42.725640045854036
905, ,  25.0, 16.1,43.6761341974838
906, ,  26.1, 16.7,45.40746013667425
907, ,  27.2, 16.7,47.12438563327032
908, ,  27.8, 16.7,48.05488494907582
909, ,  27.2, 16.1,47.12438563327032
910, ,  27.2, 15.6,47.12438563327032
911, ,  24.4, 17.8,42.725640045854036
912, ,  22.2, 17.8,39.2028901734104
913, ,  20.6, 17.8,36.60314075222954
914, ,  19.4, 17.2,34.6320607713284
915, ,  18.9, 17.2,33.80532786885246
916, ,  19.4, 17.2,34.6320607713284
917, ,  20.6, 17.8,36.60314075222954
918, ,  19.4, 15.0,34.6320607713284
919, ,  16.7, 14.4,30.129035433070868
920, ,  16.1, 15.0,29.11533149171271
921

1805, ,  6.7, 1.7,12.583094262295083
1806, ,  6.7, 2.2,12.583094262295083
1807, ,  6.7, 2.2,12.583094262295083
1808, ,  7.2, 2.8,13.494478527607363
1809, ,  6.7, 2.8,12.583094262295083
1810, ,  6.7, 3.9,12.583094262295083
1811, ,  7.2, 3.9,13.494478527607363
1812, ,  7.8, 4.4,14.583231334149325
1813, ,  11.1, 5.0,20.47735507246377
1814, ,  15.6, 1.7,28.26690391459075
1815, ,  17.8, 1.7,31.975107800862403
1816, ,  19.4, 1.1,34.6320607713284
1817, ,  20.6, -0.6,36.60314075222954
1818, ,  22.2, 1.1,39.2028901734104
1819, ,  22.8, 1.7,40.16955017301038
1820, ,  22.8, 2.8,40.16955017301038
1821, ,  22.2, 2.8,39.2028901734104
1822, ,  21.7, 4.4,38.39391891891892
1823, ,  20.6, 5.6,36.60314075222954
1824, ,  18.3, 7.8,32.80897887323944
1825, ,  16.1, 8.3,29.11533149171271
1826, ,  15.0, 8.3,27.24435196195006
1827, ,  14.4, 8.9,26.216924910607865
1828, ,  12.8, 8.9,23.453018792483004
1829, ,  12.2, 8.3,22.407414829659317
1830, ,  10.6, 8.3,19.594392900363047
1831, ,  12.2, 8.9,22.4074148296593

2707, ,  28.9, 16.7,49.74990608564989
2708, ,  28.9, 16.1,49.74990608564989
2709, ,  28.9, 17.2,49.74990608564989
2710, ,  28.9, 17.8,49.74990608564989
2711, ,  27.8, 17.8,48.05488494907582
2712, ,  25.6, 18.9,44.62228984404716
2713, ,  24.4, 19.4,42.725640045854036
2714, ,  22.8, 18.9,40.16955017301038
2715, ,  22.2, 19.4,39.2028901734104
2716, ,  20.6, 18.9,36.60314075222954
2717, ,  21.1, 19.4,37.419020897832816
2718, ,  21.7, 19.4,38.39391891891892
2719, ,  21.1, 19.4,37.419020897832816
2720, ,  19.4, 18.9,34.6320607713284
2721, ,  19.4, 18.9,34.6320607713284
2722, ,  18.9, 18.9,33.80532786885246
2723, ,  20.0, 19.4,35.61989895064128
2724, ,  20.6, 20.0,36.60314075222954
2725, ,  23.3, 19.4,40.97169992325403
2726, ,  23.9, 18.9,41.930225880551305
2727, ,  24.4, 18.3,42.725640045854036
2728, ,  26.1, 17.8,45.40746013667425
2729, ,  27.8, 17.2,48.05488494907582
2730, ,  27.8, 16.1,48.05488494907582
2731, ,  28.3, 15.6,48.82708960843373
2732, ,  26.7, 14.4,46.34573863636364
2733, ,  2

3585, ,  23.9, 22.2,41.930225880551305
3586, ,  24.4, 22.2,42.725640045854036
3587, ,  23.9, 22.8,41.930225880551305
3588, ,  25.0, 22.8,43.6761341974838
3589, ,  26.7, 22.8,46.34573863636364
3590, ,  27.2, 22.2,47.12438563327032
3591, ,  28.9, 21.7,49.74990608564989
3592, ,  30.6, 21.7,52.34210526315789
3593, ,  31.1, 20.0,53.09826751117734
3594, ,  31.7, 18.9,54.001951672862454
3595, ,  33.9, 19.4,57.28125
3596, ,  33.9, 18.3,57.28125
3597, ,  31.1, 20.6,53.09826751117734
3598, ,  30.6, 18.9,52.34210526315789
3599, ,  29.4, 21.1,50.51574803149607
3600, ,  28.3, 21.7,48.82708960843373
3601, ,  26.7, 21.1,46.34573863636364
3602, ,  23.9, 21.1,41.930225880551305
3603, ,  21.7, 21.7,38.39391891891892
3604, ,  22.2, 22.2,39.2028901734104
3605, ,  21.7, 21.7,38.39391891891892
3606, ,  22.2, 22.2,39.2028901734104
3607, ,  22.8, 22.8,40.16955017301038
3608, ,  22.2, 22.2,39.2028901734104
3609, ,  22.2, 22.2,39.2028901734104
3610, ,  21.7, 21.7,38.39391891891892
3611, ,  21.1, 21.1,37.4190208

...

135193, ,  25.9, 16.1,45.09375000000001
135194, ,  24.0, 15.8,42.089552238805965
135195, ,  23.2, 16.1,40.81151631477927
135196, ,  22.6, 16.2,39.847826086956516
135197, ,  22.4, 15.7,39.5256064690027
135198, ,  21.0, 16.3,37.25609756097561
135199, ,  20.3, 15.5,36.112092391304344
135200, ,  19.7, 15.3,35.12655642023346
135201, ,  19.2, 15.7,34.30175438596491
135202, ,  18.7, 16.3,33.47373046875
135203, ,  17.7, 16.1,31.807941176470592
135204, ,  17.4, 16.2,31.30565371024735
135205, ,  17.8, 16.4,31.975107800862403
135206, ,  18.9, 16.3,33.80532786885246
135207, ,  20.4, 15.5,36.275902211874275
135208, ,  20.9, 15.5,37.093048024786995
135209, ,  21.1, 16.3,37.419020897832816
135210, ,  21.4, 14.6,37.9070351758794
135211, ,  22.3, 12.1,39.36431047765793
135212, ,  23.8, 14.3,41.77077747989276
135213, ,  24.0, 13.6,42.089552238805965
135214, ,  24.7, 13.9,43.20143129770993
135215, ,  22.4, 15.5,39.5256064690027
135216, ,  20.6, 16.1,36.60314075222954
135217, ,  21.1, 16.3,37.419020897832

136086, ,  16.5, 15.6,29.791666666666664
136087, ,  16.9, 16.2,30.465873328088115
136088, ,  17.5, 16.9,31.473214285714285
136089, ,  20.1, 17.9,35.78409090909091
136090, ,  22.0, 18.0,38.87967605090629
136091, ,  23.0, 15.3,40.490779869381484
136092, ,  24.0, 14.4,42.089552238805965
136093, ,  24.8, 13.5,43.35978634109119
136094, ,  24.9, 13.2,43.51802059496568
136095, ,  25.1, 13.8,43.83412728658536
136096, ,  25.3, 12.6,44.149752475247524
136097, ,  24.7, 14.7,43.20143129770993
136098, ,  24.6, 14.0,43.04295532646048
136099, ,  24.2, 14.4,42.40783938814532
136100, ,  23.3, 13.5,40.97169992325403
136101, ,  22.9, 14.4,40.33022674865488
136102, ,  22.3, 14.8,39.36431047765793
136103, ,  20.4, 16.4,36.275902211874275
136104, ,  20.8, 15.5,36.92987214258039
136105, ,  20.2, 15.9,35.94815533980583
136106, ,  19.9, 15.8,35.455579315707624
136107, ,  19.8, 15.4,35.29113185530922
136108, ,  19.6, 15.8,34.96185286103542
136109, ,  19.8, 16.2,35.29113185530922
136110, ,  18.8, 16.0,33.6395939

136990, ,  4.2, 3.5,7.969565217391304
136991, ,  5.0, 4.1,9.456252579446966
136992, ,  6.0, 4.2,11.300863131935882
136993, ,  8.1, 5.4,15.125611246943764
136994, ,  8.4, 6.1,15.666666666666666
136995, ,  8.2, 7.1,15.306109979633401
136996, ,  8.2, 7.6,15.306109979633401
136997, ,  8.6, 8.0,16.026636844245626
136998, ,  9.1, 8.6,16.92400568181818
136999, ,  10.0, 9.4,18.53012535382127
137000, ,  10.7, 10.1,19.771270161290325
137001, ,  10.4, 9.6,19.24020993136859
137002, ,  11.1, 7.4,20.47735507246377
137003, ,  9.9, 4.9,18.35224514563107
137004, ,  7.9, 2.3,14.764172104404567
137005, ,  7.2, 1.4,13.494478527607363
137006, ,  5.8, -0.7,10.933155080213902
137007, ,  5.0, -1.1,9.456252579446966
137008, ,  4.6, -1.5,8.714138073584126
137009, ,  4.9, -0.8,9.270953757225433
137010, ,  5.0, -0.8,9.456252579446966
137011, ,  4.9, -1.5,9.270953757225433
137012, ,  4.8, -1.7,9.085501858736059
137013, ,  3.8, -2.3,7.222521775197013
137014, ,  3.2, -2.4,6.097297297297298
137015, ,  3.3, -2.5,6.285

137968, ,  -1.1, -3.1,-2.1341024555461474
137969, ,  -0.7, -2.9,-1.3557692307692308
137970, ,  -0.6, -2.8,-1.161596958174905
137971, ,  -1.1, -2.3,-2.1341024555461474
137972, ,  -1.2, -2.4,-2.3290978398983477
137973, ,  -1.2, -2.5,-2.3290978398983477
137974, ,  -1.1, -2.4,-2.1341024555461474
137975, ,  -1.0, -2.0,-1.939272111722387
137976, ,  -0.9, -1.7,-1.7446065989847714
137977, ,  -0.6, -1.2,-1.161596958174905
137978, ,  -0.2, -0.9,-0.3865457612821594
137979, ,  0.1, -0.6,0.19302864363942712
137980, ,  0.3, -0.3,0.5785984848484848
137981, ,  0.4, -0.1,0.771140092553639
137982, ,  0.7, 0.0,1.347794117647059
137983, ,  0.8, 0.3,1.5396892062158756
137984, ,  1.0, 0.6,1.922996223248007
137985, ,  1.1, 0.7,2.11440855704698
137986, ,  1.0, 0.7,1.922996223248007
137987, ,  1.2, 0.9,2.3056603773584907
137988, ,  1.2, 0.9,2.3056603773584907
137989, ,  1.2, 1.0,2.3056603773584907
137990, ,  1.1, 0.9,2.11440855704698
137991, ,  1.1, 0.9,2.11440855704698
137992, ,  1.2, 1.0,2.3056603773584907
1

138762, ,  21.1, 20.6,37.419020897832816
138763, ,  20.6, 20.0,36.60314075222954
138764, ,  21.7, 20.6,38.39391891891892
138765, ,  22.8, 21.1,40.16955017301038
138766, ,  22.2, 18.3,39.2028901734104
138767, ,  22.8, 16.1,40.16955017301038
138768, ,  23.9, 15.0,41.930225880551305
138769, ,  25.0, 14.4,43.6761341974838
138770, ,  25.6, 10.0,44.62228984404716
138771, ,  25.0, 8.3,43.6761341974838
138772, ,  23.3, 6.7,40.97169992325403
138773, ,  21.1, 6.7,37.419020897832816
138774, ,  19.4, 8.9,34.6320607713284
138775, ,  18.9, 10.6,33.80532786885246
138776, ,  17.8, 11.1,31.975107800862403
138777, ,  17.2, 11.7,30.97013752455796
138778, ,  16.7, 11.7,30.129035433070868
138779, ,  15.6, 11.7,28.26690391459075
138780, ,  15.0, 12.2,27.24435196195006
138781, ,  15.0, 12.8,27.24435196195006
138782, ,  16.1, 12.8,29.11533149171271
138783, ,  16.1, 12.8,29.11533149171271
138784, ,  15.6, 12.2,28.26690391459075
138785, ,  14.4, 12.2,26.216924910607865
138786, ,  15.0, 12.2,27.24435196195006
13

# Converting
For modeling stage, one needs to prepare the data. Depending on the choice of model algorithm one may require all features to be converted to numerical equivalent values. So for instance converting text categorical values to numeric values.

In [47]:
# Converting timestamp from object to datetime

combined = [train_df, test_df, weather_train_df, weather_test_df]

for df in combined:
    df['timestamp'] = pd.to_datetime(df['timestamp'], infer_datetime_format=True)

In [53]:
# Mapping primary_use category in building metadata

primary_use_map = {'Education': 1, 'Office': 2, 'Entertainment/public assembly': 3, 'Lodging/residential': 4,
                   'Public services': 5, 'Healthcare': 6, 'Other': 7, 'Parking': 8, 'Manufacturing/industrial': 9,
                   'Food sales and service': 10, 'Retail': 11, 'Warehouse/storage': 12, 'Services': 13, 
                   'Technology/science': 14, 'Utility': 15, 'Religious worship': 16}

building_df['primary_use'] = building_df['primary_use'].map(primary_use_map).astype(np.int64)

# Correlating
One can approach the problem based on available features within the training dataset. Which features within the dataset contribute significantly to our solution goal? Statistically speaking is there a correlation among a feature and solution goal? As the feature values change does the solution state change as well, and visa-versa? This can be tested both for numerical and categorical features in the given dataset. We may also want to determine correlation among features other than survival for subsequent goals and workflow stages. Correlating certain features may help in creating, completing, or correcting features.

In [67]:
train_merged['wind_direction']

0             0.0
1             0.0
2             0.0
3             0.0
4             0.0
            ...  
20216095    180.0
20216096    180.0
20216097    180.0
20216098    180.0
20216099    180.0
Name: wind_direction, Length: 20216100, dtype: float64

In [63]:
train_merged.loc[train_merged['meter']==3]

building_id  meter           timestamp  meter_reading  site_id  primary_use  square_feet  air_temperature  dew_temperature  wind_direction  wind_speed  relative_humidity
105               106      3 2016-01-01 00:00:00          0.000        1            1         5374              3.8              2.4           240.0         3.1               63.5
109               109      3 2016-01-01 00:00:00          0.000        1            1        56995              3.8              2.4           240.0         3.1               63.5
113               112      3 2016-01-01 00:00:00         96.978        1            1        32206              3.8              2.4           240.0         3.1               63.5
115               113      3 2016-01-01 00:00:00         19.597        1            1       100481              3.8              2.4           240.0         3.1               63.5
117               114      3 2016-01-01 00:00:00        100.000        1            1       139683              3.8              2.4           240.0         3.1               63.5
...               ...    ...                 ...            ...      ...          ...          ...              ...              ...             ...         ...                ...
20215844         1322      3 2016-12-31 23:00:00       2476.610       14            3       166489              6.1             -6.7           190.0         9.8             -115.9
20215847         1323      3 2016-12-31 23:00:00       1909.330       14            2        87200              6.1             -6.7           190.0         9.8             -115.9
20215850         1324      3 2016-12-31 23:00:00        364.019       14            3        84688              6.1             -6.7           190.0         9.8             -115.9
20215852         1325      3 2016-12-31 23:00:00        156.050       15            3       155177              1.7             -5.6           180.0         8.8             -339.8
20215867         1331      3 2016-12-31 23:00:00       8501.020       15            1       171008              1.7             -5.6           180.0         8.8             -339.8

[1264037 rows x 12 columns]

In [62]:
# Merge dataframes

train_merged = train_df.merge(building_df, on='building_id', how='left')
train_merged = train_merged.merge(weather_train_df, on=['site_id', 'timestamp'], how='left')

test_merged = test_df.merge(building_df, on='building_id', how='left')
test_merged = test_merged.merge(weather_test_df, on=['site_id', 'timestamp'], how='left')

# Model, predict and solve
Now we are ready to train a model and predict the required solution. There are 60+ predictive modelling algorithms to choose from. We must understand the type of problem and solution requirement to narrow down to a select few models which we can evaluate. Our problem is a classification and regression problem. We are also performing a category of machine learning which is called supervised learning as we are training our model with a given dataset. With these two criteria - Supervised Learning plus Classification and Regression, we can narrow down our choice of models to a few.